In [12]:
%run "libraries.ipynb"

from IPython.display import display, HTML
from IPython.html import widgets
import matplotlib.patheffects as path_effects

In [13]:
g = nx.read_gexf("data/reading_maps/pages-hyperlinks-reduced-3.gexf")

## community detection

In [14]:
import community
partitions = community.best_partition(g.to_undirected())

In [15]:
def print_groups(communities):
    html = "<table>"

    for c, ps in communities.iteritems():
        html += "<tr><td style=\"width: 100px; text-align: center; \"><h3>group %s</h3></td><td>" % (c)
        html += ", ".join(map(lambda x: u"<a href=\"http://en.wikipedia.org/wiki/{0}\" target=\"_blank\">{0}</a>".format(x), ps))
        html += "</td></tr>"
    
    html += "</table>"

    display(HTML(html))
        
communities = {}
for k, v in partitions.iteritems():
    communities.setdefault(v, []).append(k)


print_groups(communities)

## subgraphs explorer

In [16]:
%config InlineBackend.figure_formats=['svg']

def map_colors(g ,partitions):
    size = np.max( [ x[1] for x in partitions.iteritems() ])
    
    for n in partitions:
        g.node[n]["color"] = float(partitions[n])/float(size)


map_colors(g, partitions)

In [36]:
pages = g.nodes()
pages = sorted(pages)

color_map = plt.get_cmap("Set2")

n_extension = 2

def display_local_graph(page, range_of_network):
    nbunch = [ page ]
    
    # moche, faut me refactorer ça
    for _ in range(0,range_of_network):
        nb = []
        for p in nbunch:
            nb.extend( list(g.to_undirected()[p]) )
        nbunch.extend(nb)

    g_sub = g.subgraph(nbunch)
    
    #nx.draw_spring(g2)
    pos = nx.spring_layout(g_sub,iterations=150, weight="term occurence", k=20)
   
    plt.figure(figsize=(12,12))

    colors = map(lambda x: g.node[x]["color"], g_sub.nodes())
    
    # draw nodes
    nodes = nx.draw_networkx_nodes(g_sub, pos, alpha=0.9, node_size=500, node_color=colors, cmap=color_map, vmin=0, vmax=1)
    nodes.set_edgecolor('w')

    # draw edges
    nx.draw_networkx_edges(g_sub, pos, alpha=0.3, width=1)
    
    # draw labels
    labels = nx.draw_networkx_labels(g_sub, pos, font_size=8, font_family="Bitstream Vera Sans")
    map(lambda x: labels[x].set_path_effects([path_effects.Stroke(linewidth=1, foreground='white'),
                       path_effects.Normal()]),labels)
    
    plt.axis('off')
    plt.show()


w = widgets.Select(description="page", options=pages)
widgets.interact(display_local_graph, page=w, range_of_network=(1,3));